# Como analisar dados de Futebol

Neste vídeo eu trago uma introdução sobre como, no geral, você irá encontrar os dados de futebol. Os tipos de tabelas e como unir todas elas.

Espero que ajude a sua jornada de conhecimento.

Link para download da base de dados: https://www.kaggle.com/tiagodatascience/campeonato-paulista-a1

Link para o vídeo do Youtube: https://www.youtube.com/watch?v=5AwqRsMtkCo&t=637s



In [13]:
import datetime
import pandas as pd
import betfairlightweight
import time
pd.set_option('display.max_columns',50)

In [14]:
df_jogos = pd.read_csv('../dados/jogos_paulista.csv')
df_stats = pd.read_csv('../dados/stats_paulista.csv')
df_eventos = pd.read_csv('../dados/events_paulista.csv')

# Tabela de Jogos

- 1 jogo por linha
- Dados como o estádio, juiz, resultado, id do jogo, nome dos times, etc.
- Base para a união dos dados para as demais tabelas

In [15]:
df_jogos.columns

Index(['idEvent', 'dateEvent', 'eventCity', 'eventStatus', 'eventElapsed',
       'eventLeague', 'eventRound', 'idHomeTeam', 'strHomeTeam',
       'logoHomeTeam', 'idAwayTeam', 'strAwayTeam', 'logoAwayTeam',
       'intHomeScore', 'intAwayScore', 'intHomeHt', 'intAwayHt', 'date',
       'hour', 'idWinner', 'winner', 'winOrDraw', 'underOver', 'predGoalsHome',
       'predGoalsAway', 'advice', 'formHome', 'formAway', 'attHome', 'attAway',
       'defHome', 'defAway', 'poissonHome', 'poissonAway', 'h2hHome',
       'h2hAway', 'goalsHome', 'goalsAway', 'totalHome', 'totalAway',
       'homeOdd', 'drawOdd', 'awayOdd', 'over05', 'over05Ht', 'under15',
       'under15Ht'],
      dtype='object')

In [16]:
df_jogos.head()

idEvent                  dateEvent                  eventCity  \
0   317888  2020-02-02 19:00:00-03:00        Campinas, São Paulo   
1   317890  2020-02-03 20:00:00-03:00  Ribeirão Preto, São Paulo   
2   317891  2020-02-03 20:00:00-03:00       São Paulo, São Paulo   
3   317892  2020-02-07 19:15:00-03:00         Barueri, São Paulo   
4   317907  2020-02-21 16:00:00-03:00  Ribeirão Preto, São Paulo   

      eventStatus  eventElapsed    eventLeague          eventRound  \
0  Match Finished            90  Paulista - A1  Regular Season - 4   
1  Match Finished            90  Paulista - A1  Regular Season - 4   
2  Match Finished            90  Paulista - A1  Regular Season - 4   
3  Match Finished            90  Paulista - A1  Regular Season - 5   
4  Match Finished            90  Paulista - A1  Regular Season - 7   

   idHomeTeam       strHomeTeam  \
0         138  Guarani Campinas   
1        2618       Botafogo SP   
2         126         Sao Paulo   
3         143             Oeste   
4        2618       Botafogo SP   

                                        logoHomeTeam  idAwayTeam  \
0  https://media.api-sports.io/football/teams/138...       10003   
1  https://media.api-sports.io/football/teams/261...        7848   
2  https://media.api-sports.io/football/teams/126...        7834   
3  https://media.api-sports.io/football/teams/143...         138   
4  https://media.api-sports.io/football/teams/261...        1201   

        strAwayTeam                                       logoAwayTeam  \
0       Santo André  https://media.api-sports.io/football/teams/100...   
1          Mirassol  https://media.api-sports.io/football/teams/784...   
2     Novorizontino  https://media.api-sports.io/football/teams/783...   
3  Guarani Campinas  https://media.api-sports.io/football/teams/138...   
4  Inter De Limeira  https://media.api-sports.io/football/teams/120...   

   intHomeScore  intAwayScore  intHomeHt  intAwayHt                 date  \
0             2             1          1          1  2020-02-02 00:00:00   
1             0             6          0          3  2020-02-03 00:00:00   
2             1             1          0          0  2020-02-03 00:00:00   
3             1             1          1          1  2020-02-07 00:00:00   
4             2             1          0          1  2020-02-21 00:00:00   

       hour  idWinner            winner  winOrDraw  underOver  predGoalsHome  \
0  19:00:00   10003.0       Santo André      False        1.5           -2.5   
1  20:00:00    7848.0          Mirassol       True        0.0           -1.5   
2  20:00:00    7834.0     Novorizontino       True       -3.5           -2.5   
3  19:15:00     138.0  Guarani Campinas      False        1.5           -1.5   
4  16:00:00    1201.0  Inter De Limeira       True        0.0           -1.5   

   predGoalsAway                                             advice  formHome  \
0           -4.5          Combo Winner : Santo André and +1.5 goals        31   
1           -1.5                   Double chance : draw or Mirassol        25   
2           -2.5  Combo Double chance : draw or Novorizontino an...        50   
3           -4.5     Combo Winner : Guarani Campinas and +1.5 goals        30   
4           -2.5           Double chance : draw or Inter De Limeira        18   

   formAway  attHome  attAway  defHome  defAway  poissonHome  poissonAway  \
0        69       50       50       50       50           24           76   
1        75       50       50       30       70            0          100   
2        50       50       50        0      100            0            0   
3        70       20       80       27       73            8           92   
4        82       43       57       25       75           10           90   

   h2hHome  h2hAway  goalsHome  goalsAway  totalHome  totalAway  homeOdd  \
0        0        0          0          0       38.8       61.3      0.0   
1        0        0          0          0       35.0       65.0     

# Tabela Estatísticas

- Pode variar, neste caso são 2 linhas por jogo (1 para o time da casa e 1 para o visitante)
- Trazem os dados como posse de bola, chutes a gol, escanteios, cartões, etc.
- Com os tratamentos, transformando 1 linha por jogo, geralmente é o input para análises e modelos estatísticos

In [11]:
df_stats.head()

idEvent  idTeam      strTeam  isHome  shots_on_goal  shots_off_goal  \
0   317952   10018   Água Santa    True            4.0             3.0   
1   317952    7826  Ferroviária   False            2.0             7.0   
2   317953    2618  Botafogo SP    True            5.0             3.0   
3   317953   10018   Água Santa   False            5.0             4.0   
4   317954   10018   Água Santa    True            2.0             2.0   

   total_shots  blocked_shots  shots_insidebox  shots_outsidebox  fouls  \
0         11.0            4.0              6.0               5.0   15.0   
1         17.0            8.0              8.0               9.0   13.0   
2         12.0            4.0             10.0               2.0   18.0   
3         13.0            4.0              8.0               5.0   10.0   
4          5.0            1.0              3.0               2.0   20.0   

   corner_kicks  offsides ball_possession  yellow_cards  red_cards  \
0           7.0       1.0             42%           1.0        NaN   
1           8.0       NaN             58%           3.0        NaN   
2           7.0       1.0             60%           4.0        NaN   
3           5.0       NaN             40%           3.0        NaN   
4           1.0       3.0             35%           6.0        NaN   

   goalkeeper_saves  total_passes  passes_accurate passes_%  
0               3.0         312.0            242.0      78%  
1               3.0         418.0            334.0      80%  
2               4.0         478.0            394.0      82%  
3               4.0         307.0            239.0      78%  
4               5.0         305.0            240.0      79%

# Tabela Eventos

- 1 linha por tipo de evento/time/jogador/tempo
- Geralmente traz os principais eventos do jogos: Substituições, cartões, gols
- Interessante para montar uma linha do tempo do jogo e entender o efeito destes eventos no resultado. Será que um cartão vermelho acima dos 30 minutos garante que o time com 1 a mais será vencedor? Fica a questão para análises...hehe

In [12]:
df_eventos.head()

idEvent  timeElapsed  idTeam      strTeam  idPlayer       strPlayer   tipo  \
0   317952           32    7826  Ferroviária     15278          Carlão   Card   
1   317952           40    7826  Ferroviária      9457           Rayan  subst   
2   317952           55   10018   Água Santa     55298        Uederson  subst   
3   317952           59    7826  Ferroviária     80600            Tony   Card   
4   317952           65   10018   Água Santa      9852  Felipe Azevedo  subst   

           detail comments  
0     Yellow Card      NaN  
1  Substitution 1      NaN  
2  Substitution 1      NaN  
3     Yellow Card      NaN  
4  Substitution 2      NaN